In [ ]:
json_data = {"type":"FeatureCollection","features": []}
for fname in os.listdir('geojson'):
    if 'json' in fname:
        data = json.load(open(f'geojson/{fname}', 'r'))
        json_data['features'].extend(data['features'])

In [ ]:
combined_json = 'geojson/combined.geojson'
json.dump(json_data, open(combined_json, 'w'))

In [ ]:
ny_json = 'geojson/ny_new_york_zip_codes_geo.min.json'
ca_json = 'geojson/ca_california_zip_codes_geo.min.json'
il_json = 'geojson/il_illinois_zip_codes_geo.min.json'

In [333]:
import folium
import json
import numpy as np
import pandas as pd
from IPython.display import display
import pprint as pp
import os
import re
import pprint as pp
import matplotlib.pyplot as plt
from utils import *
import tqdm
import pickle
from geopy.geocoders import Nominatim
geolocator = Nominatim(user_agent="geoapiExercises")

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
from IPython.core.display import display, HTML
display(HTML("<style>.container { width:80% !important; }</style>"))

In [3]:
df2 = pd.read_csv('h1b_raw_data_2019.csv')

/home/jingbo/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3063: DtypeWarning: Columns (5,14,15,21,23,27,28,29,30,32,33,34,35,36,37,38,39,40,41,42,43,44,46,47,48,49,58,59,60,62,65,67,68,69,70,71,72,73,74,77,79,80,81,83,86,88,89,90,91,92,93,94,95,98,99,100,101,102,104,107,109,110,111,112,113,114,115,116,122,123,125,128,130,131,132,133,134,135,136,137,143,144,146,149,151,152,153,154,155,156,157,158,161,163,164,165,167,170,172,173,174,175,176,177,178,179,185,186,188,191,193,194,195,196,197,198,199,200,206,207,209,212,214,215,216,217,218,219,220,221,224,226,227,228,230,233,235,236,237,238,239,240,241,245,247,248,249,251,254,258,259,260) have mixed types.Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [4]:
hourly_lookup = {
    'Year': 2080,
    'Hour': 1, 
    'Bi-Weekly': 80,
    'Month': 40 * 4 + 12,  # 172
    'Week': 40,
}

In [48]:
def cleanup_zip(code):
    #if ';' in code:
    #    return code.split(';')[-1]
    #elif '-' in code:
    #    return code.split('-')[0]
    #elif ',' in code:
    #    return code.split(',')[-1]
    code = re.sub('[^0-9]', '', code)[:5]

    return code

def cleanup_soc_code(code):
    #if ';' in code:
    #    return code.split(';')[-1]
    #elif '-' in code:
    #    return code.split('-')[0]
    #elif ',' in code:
    #    return code.split(',')[-1]
    # code = re.sub('[^0-9]', '', code)[:5]
    code = code.split('.')[0]

    return code

def get_soc_title_lookup(dirty_soc_title):
    processed = re.sub('[^A-Za-z\s]', '', dirty_soc_title.strip())
    processed = re.sub('[Ss]$', '', processed.strip())
    processed = re.sub('\s+', ' ', processed.strip())
    return processed

def get_state_abbrev(state):
    if len(state) == 2:
        return state.upper()
    elif state.lower().title() in STATE_ABBREV_LOOKUP:
        return STATE_ABBREV_LOOKUP[state.lower().title()]
    elif state.lower().title() == 'District Of Columbia':
        return 'DC'
    else:
        #print(state)
        return ''

# RE_ADDR = re.compile(r"(one|[0-9]+)\,?\s+([nswe]?\.?\s+)?([\w\'\.\/]+\s)*([\w\.]+\s?)")
RE_CITY = re.compile(r"^([a-zA-Z\']+(\.|\,)(\s?|\-))?(([a-zA-Z\']+(\s+|\-))*)([a-zA-Z\']+)$")
def city_regex(string):
    string_new = string.replace('&nbsp;', '')
    string_new = string_new.replace(',', '')
    string_new = string_new.replace('D.C.', '')
    result = RE_CITY.search(string_new.strip())
    if result is not None:
        return result[0].title()
    return ''

# RE_ADDR = re.compile(r"(one|[0-9]+)\,?\s+([nswe]?\.?\s+)?([\w\'\.\/]+\s)*([\w\.]+\s?)")
RE_ADDR = re.compile(r"((one|two|three|four|five|[0-9]+)\s?\,?\-?\s*([nswe]?\.?\s+)?(([\w|\'|\.|\/]+\s+)*)((\w*[\'|'\.|\/]?[a-zA-Z]+\s?)|([a-zA-Z][0-9]+\s?)))($|\W)")
def address_regex(string):
    result = RE_ADDR.search(string)
    if result is not None:
        return result[1].title().replace('-', ' ')
    return None


def get_clean_street_address(addr1, addr2):
    
    parsed1 = address_regex(addr1.lower())
    parsed2 = address_regex(addr2.lower())
    
    if parsed2 == None and parsed1 != None:
        return parsed1
    elif parsed1 == None and parsed2 != None:
        return parsed2
    elif parsed1 != None and parsed2 != None:
        return parsed1
    else:
        if addr1 != 'nan' or addr2 != 'nan':
            #print(addr1, ' ----- ', addr2)
            pass
        return ''

def addr_abbrev_replace(string):
    string = string.strip()
    string = string.replace(',', '')
    
    string = re.sub(r'\s+Dr\.?$', ' Drive', string)
    string = re.sub(r'\s+Rd\.?$', ' Road', string)
    string = re.sub(r'\s+Ct\.?$', ' Court', string)
    string = re.sub(r'\s+Sq\.?$', ' Square', string)
    string = re.sub(r'\s+Ln\.?$', ' Lane', string)
    string = re.sub(r'\s+Blvd\.?$', ' Boulevard', string)
    string = re.sub(r'\s+Pl\.?$', ' Place', string)
    string = re.sub(r'\s+St\.?$', ' Street', string)
    string = re.sub(r'\s+Ave\.?$', ' Avenue', string)
    string = re.sub(r'\s+Ctr\.?$', ' Center', string)
    string = re.sub(r'\s+Pkwy\.?$', ' Parkway', string)
    string = re.sub(r'\sCentre\s$', ' Center ', string)
    
    string = re.sub(r'\s+', ' ', string)
    return string


In [291]:
def company_name_replace(candidate, n):
    
    def internal(string):
        string = string.lower().strip()
        string = re.sub(r'(\,\s*|\s+)p(\.)?l(\.)?l(\.)?c(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)p(\.)?l(\.)?c(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)l(\.)?l(\.)?c(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)l(\.)?p(\.)?a(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)a(\.)?p(\.)?c(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)l(\.)?l(\.)?p(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)l(\.)?l(\.)?o(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)l(\.)?c(\.)?c(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)u(\.)?s(\.)?a(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)inc(\.)?($|\W)', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)corp(\.)?($|\W)', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)assc(\.)?($|\W)', ' associates', string).strip()
        string = re.sub(r'(\,\s*|\s+)l(\.)?t(\.)?d(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)l(\.)?p(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)p(\.)?a(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)p(\.)?c(\.)?$', '', string).strip()
        string = re.sub(r'(\,\s*|\s+)o(\.)?d(\.)?$', '', string).strip()
        #string = re.sub(r'(\,)?\s+l(\.)$', '', string)
        #string = re.sub(r'(\,)?\s+p(\.)$', '', string)
        string = re.sub(r'(\(.*(\)|$))', '', string).strip()
        # string = re.sub(r'(\s+[a-zA-Z]\.\s+)', '', string).strip()
        string = re.sub(r'\.$', '', string).strip()
        string = re.sub(r'\-', ' ', string).strip()
        string = re.sub(r'group$', '', string).strip()
        string = re.sub(r'corporation$', '', string).strip()
        string = re.sub(r'incorporated$', '', string).strip()
        string = re.sub(r'group$', '', string).strip()
        string = re.sub(r'americas$', '', string).strip()
        string = re.sub(r'\s+us$', '', string).strip()
        string = re.sub(r'\&', 'and', string).strip()
        string = re.sub(r'\,\s+and\s+', ' and ', string).strip()
        string = re.sub(r'\s+([A-Za-z])\.?\s+', r' \1. ', string)
        string = re.sub(r'\s+', ' ', string).strip()

        return string.title().strip()
    
    result = candidate
    for i in range(n):
        result = internal(result)
    
    return result

In [326]:
def get_okay_hourly(h):
    def hourly_okay(v):
        return v > 7.25 and v < 5000

    h2 = h
    if hourly_okay(h2):
        return h2

    for schedule in ['Year', 'Month', 'Bi-Weekly', 'Week']:
        h2 = h / hourly_lookup[schedule]
        if hourly_okay(h2):
            return h2
    
    return 7.25

def get_okay_wage(wage, unit):    
    if unit in hourly_lookup:
        hourly = wage / hourly_lookup[unit]
    else:
        hourly = wage / hourly_lookup['Year']
    hourly = get_okay_hourly(hourly)

    yearly = hourly * hourly_lookup['Year']
    return yearly

In [327]:
clean_data = []
soc_code_lookup = {}
for i, row in tqdm.tqdm(df2.iterrows(), total=len(df2), miniters=int(50000)):
    
    data = {
        'VISA_CLASS': str((row['VISA_CLASS'])),
        'CASE_STATUS': str((row['CASE_STATUS'])),
        'SOC_TITLE': get_soc_title_lookup(str((row['SOC_TITLE']))),
        'SOC_CODE': cleanup_soc_code(str((row['SOC_CODE']))),
        'NAICS_CODE': str((row['NAICS_CODE'])),
        'EMPLOYER_NAME': company_name_replace(str((row['EMPLOYER_NAME'])), 2),
        'AGENT_ATTORNEY_LAW_FIRM': company_name_replace(str((row['AGENT_ATTORNEY_LAW_FIRM_BUSINESS_NAME'])), 2),
        'WORKSITE_ADDRESS1': str((row['WORKSITE_ADDRESS1_1'])),
        'WORKSITE_ADDRESS2': str((row['WORKSITE_ADDRESS2_1'])),
        'WORKSITE_CITY': str((row['WORKSITE_CITY_1'])),
        'WORKSITE_COUNTY': str((row['WORKSITE_COUNTY_1'])),
        'WORKSITE_STATE': get_state_abbrev(str((row['WORKSITE_STATE_1']))),
        'WORKSITE_POSTAL_CODE': cleanup_zip(str((row['WORKSITE_POSTAL_CODE_1']))),
        'WAGE_RATE_OF_PAY_FROM': float(row['WAGE_RATE_OF_PAY_FROM_1']),
        'WAGE_RATE_OF_PAY_TO': float(row['WAGE_RATE_OF_PAY_TO_1']),
        'WAGE_UNIT_OF_PAY': str((row['WAGE_UNIT_OF_PAY_1'])),
        'PREVAILING_WAGE': float(row['PREVAILING_WAGE_1']),
        'PW_UNIT_OF_PAY': str((row['PW_UNIT_OF_PAY_1'])),
        'PW_TRACKING_NUMBER': str((row['PW_TRACKING_NUMBER_1'])),
        'PW_WAGE_LEVEL': str((row['PW_WAGE_LEVEL_1'])),
        'PW_OES_YEAR': str((row['PW_OES_YEAR_1'])),
        'PW_OTHER_SOURCE': str((row['PW_OTHER_SOURCE_1'])),
        'PW_NON-OES_YEAR': str((row['PW_NON-OES_YEAR_1'])),
    }

    if data['SOC_CODE'] not in soc_code_lookup:
        soc_code_lookup[data['SOC_CODE']] = set()
    soc_code_lookup[data['SOC_CODE']].add(data['SOC_TITLE'])

    data['WAGE_RATE_ANNUAL'] = get_okay_wage(data['WAGE_RATE_OF_PAY_FROM'], data['WAGE_UNIT_OF_PAY'])
    data['PREVAILING_WAGE_RATE_ANNUAL'] = get_okay_wage(data['PREVAILING_WAGE'], data['PW_UNIT_OF_PAY'])
    
    data['WORKSITE_ADDRESS_CLEAN'] = addr_abbrev_replace(get_clean_street_address(data['WORKSITE_ADDRESS1'], data['WORKSITE_ADDRESS2']))
    data['WORKSITE_CITY_CLEAN'] = city_regex(data['WORKSITE_CITY'])
    clean_data.append(data)
    #if i > 50 * 1000:
    #    break
    
clean_df = pd.DataFrame(clean_data)










  0%|          | 0/664616 [00:00<?, ?it/s]








  8%|▊         | 50000/664616 [00:27<05:41, 1800.09it/s]








 15%|█▌        | 100000/664616 [00:48<04:50, 1943.42it/s]








 23%|██▎       | 150000/664616 [01:09<04:08, 2068.59it/s]








 30%|███       | 200000/664616 [01:29<03:34, 2169.85it/s]








 38%|███▊      | 250000/664616 [01:50<03:05, 2229.83it/s]








 45%|████▌     | 300000/664616 [02:11<02:40, 2272.32it/s]








 53%|█████▎    | 350000/664616 [02:32<02:16, 2301.33it/s]








 60%|██████    | 400000/664616 [02:54<01:54, 2313.38it/s]








 68%|██████▊   | 450000/664616 [03:15<01:32, 2322.65it/s]








 75%|███████▌  | 500000/664616 [03:36<01:10, 2337.66it/s]








 83%|████████▎ | 550000/664616 [03:58<00:49, 2325.60it/s]








 90%|█████████ | 600000/664616 [04:20<00:27, 2308.09it/s]








100%|██████████| 664616/664616 [04:48<00:00, 2300.65it/s]


In [102]:
unique_full_addr = list(zip(clean_df['WORKSITE_ADDRESS_CLEAN'], clean_df['WORKSITE_CITY_CLEAN'], clean_df['WORKSITE_POSTAL_CODE']))

In [286]:
company_name_replace('Law Office Of Thomas V Allen')

'Law Office Of Thomas V. Allen'

In [287]:
# company_names = [company_name_replace(company_name_replace(d)) for d in clean_df['EMPLOYER_NAME'].unique()]
company_names = [company_name_replace(company_name_replace(d)) for d in clean_df['AGENT_ATTORNEY_LAW_FIRM'].unique()]
company_names = set(company_names)

In [313]:
df2['VISA_CLASS'].unique()

array(['H-1B', 'E-3 Australian', 'H-1B1 Singapore', 'H-1B1 Chile'],
      dtype=object)

In [342]:
pickle.dump(soc_code_lookup, open('soc_code_lookup.pickle', 'wb'))

In [129]:
sorted(clean_df['EMPLOYER_NAME'].unique())

["'PROFESSIONAL AND SCIENTIFIC ASSOCIATES, INC.",
 '(AMBI)DEXTROUS ASSET MANAGEMENT LLC',
 '+VANTAGE CORPORATION',
 '01INTERACTIVE, INC.',
 '05MEDIA, INC.',
 '0965688 BC LTD',
 '1',
 '1 DEBIT, INC.',
 '1 DUST TECHNOLOGY LLC',
 '1 HOTEL SOUTH BEACH, INC.',
 '1 LOWFLYER INC.',
 '1 MODEL MANAGEMENT, LLC',
 '1 SOURCE CONSULTING, INC.',
 '1 WAY SOLUTIONS, INC.',
 '1-800-FLOWERS.COM, INC.',
 '1-800-PUBLICRELATIONS, INC',
 '10 BITS LLC',
 '100 KEYS LLC',
 '100 THIEVES LLC',
 '1000HEADS, INC.',
 '101 LUXURY TRANSPORTATION INC.',
 '101 STUDIOS, LLC',
 '101 THERAPY STAFFING INC',
 '1010 DATA',
 '1010DATA',
 '1010DATA, INC.',
 '1052 PARTNERS LLC',
 '106 VERNAL ST LLC',
 '10BITS LLC',
 '10TH LANE PARTNERS, L.P.',
 '10TH LANE PARTNERS, LP',
 '10X GENOMICS, INC',
 '10X GENOMICS, INC.',
 '10X GENOMICS. INC.',
 '10X SYS INC',
 '10XBETA LLC',
 '10XTS INC.',
 '11 2 CAPITAL MANAGEMENT, LLC',
 '11 HEALTH AND TECHNOLOGIES INC.',
 '11-7 RECORDING CORP',
 '110 HOLDINGS LLC',
 '1100 ARCHITECT PC',
 '11061987 

In [104]:
unique_addrs, unique_addr_counts = np.unique(unique_full_addr, return_counts=True, axis=0)
sorted_unique_addr_count_args = np.argsort(unique_addr_counts)[::-1]

In [77]:
unique_addrs

array([['', '', ''],
       ['', '', '08852'],
       ['', '', '10003'],
       ...,
       ['Tworks Inc', 'Sunnyvale', '94089'],
       ['Tworth', 'Dover', '3820'],
       ['Tworx', 'Dallas', '75234']], dtype='<U50')

In [340]:
get_gps('San Jose')

(37.3361905, -121.8905833)

In [ ]:
address_lookup = {}

In [125]:
for i in tqdm.tqdm(range(1900, 5000), miniters=int(60)):
    orig_index = sorted_unique_addr_count_args[i]
    # print(f'{unique_addrs[orig_index]}: {unique_addr_counts[orig_index]}')
    
    search_string = ' '.join(unique_addrs[orig_index])
    gps = get_gps(search_string)
    # print(gps)
    
    address_lookup[tuple(unique_addrs[orig_index])] = gps










  0%|          | 0/3100 [00:11<?, ?it/s]


GeocoderUnavailable: HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Max retries exceeded with url: /search?q=1664+N.+Virginia+Street+Reno+89557&format=json&limit=1 (Caused by ReadTimeoutError("HTTPSConnectionPool(host='nominatim.openstreetmap.org', port=443): Read timed out. (read timeout=1)"))

In [119]:
len(address_lookup)

1912

In [124]:
pickle.dump(address_lookup, open('address_gps.pickle', 'wb'))

In [116]:
print(len(unique_addr_counts[sorted_unique_addr_count_args]))
print(sum(unique_addr_counts[sorted_unique_addr_count_args][:5000]))

125992
359549


In [294]:
unique_addr_counts[sorted_unique_addr_count_args][1900]

52

In [7]:
unique_addr = list(clean_df['WORKSITE_ADDRESS_CLEAN'].unique())

In [26]:
pp.pprint(sorted(list(clean_df['WORKSITE_CITY'].unique())))

['# 19820 Detroit MSA',
 '# 47644 MI METRO DIVISION',
 '#19100 DALLAS MSA',
 '#19100 Dallas MSA',
 '#19100 Dallas TX MSA',
 '#1980 DETROIT MSA',
 '#19820 DETROIT MSA',
 '#19820 Detroit MSA',
 '#19820 TROY MSA',
 '#19820 Troy MSA',
 '#29404 IL-WI Metro Division',
 '#310',
 '#41740 SAN DIEGO CA MSA',
 '#47644 MI METRO DIVISION',
 '&nbsp;Alpharetta',
 '&nbsp;Chicago',
 '&nbsp;Durham',
 '&nbsp;Houston',
 '&nbsp;New York',
 '&nbsp;Oklahoma City',
 '&nbsp;Philadelphia',
 '(East 149th Street)',
 ', 120 Mallard Street',
 ', Columbus',
 ', Deerfield',
 ', Durham',
 ', East Hartford',
 ', Phoenix',
 ', SAN JOSE',
 ',AUSTIN',
 ',Deerfield',
 ',SAINT LOUIS',
 ',SUNNYVALE',
 ',San Jose',
 ',San leandro',
 '.Philadelphia',
 '1 New York Plaza',
 '100 Nassau Park Blvd',
 '1000 SUMMIT DRIVE',
 '10004',
 '10010',
 '10011',
 '101 METLIFE WAY',
 '1050 WOODWARD AVE',
 '111 8th Avenue',
 '120 MCGINTY COURT, CLEMSON',
 '12135 Brockton Lane North',
 '12TH  FLOOR',
 '130 S 9th St',
 '13850',
 '13th Floor',
 '1

 'FINDLAY',
 'FINDLEY LAKE',
 'FINKSBURG',
 'FISHERS',
 'FITCHBURG',
 'FITZGERALD',
 'FIndlay',
 'FLAGLER BEACH',
 'FLAGSTAF',
 'FLAGSTAFF',
 'FLANDERS',
 'FLAT ROCK',
 'FLEMINGTON',
 'FLINT',
 'FLOOR 19',
 'FLOOR 6',
 'FLOOR 8',
 'FLORA',
 'FLORAL PARK',
 'FLORENCE',
 'FLORHAM PARK',
 'FLOSSMOOR',
 'FLOWER MOUND',
 'FLOWERY BRANCH',
 'FLOWOOD',
 'FLUSHING',
 'FOGELSVILLE',
 'FOLEY',
 'FOLSOM',
 'FOND DU LAC',
 'FONTANA',
 'FOOTHILL RANCH',
 'FOOTHILLS RANCH',
 'FORDS',
 'FOREST',
 'FOREST CITY',
 'FOREST GROVE',
 'FOREST HILL',
 'FOREST HILLS',
 'FOREST LAKE',
 'FOREST PARK',
 'FORESTER CITY',
 'FORNEY',
 'FORSYTH',
 'FORT CALHOUN',
 'FORT COLLINGS',
 'FORT COLLINS',
 'FORT DEPOSIT',
 'FORT DODGE',
 'FORT LAUDERDALE',
 'FORT LAUDERDALE FL',
 'FORT LAuDERDALE',
 'FORT LEE',
 'FORT MADISON',
 'FORT MILL',
 'FORT MILL,',
 'FORT MILLS',
 'FORT MORGAN',
 'FORT MYERS',
 'FORT Mill',
 'FORT OGLETHORPE',
 'FORT PAYNE',
 'FORT PIERCE',
 'FORT RECOVERY',
 'FORT SMITH',
 'FORT SNELLING',
 'FORT 

 'Mountain VIew',
 'Mountain View',
 'Mountain View Lane',
 'Mountain View,',
 'Mountain house',
 'Mountain view',
 'MountainView',
 'Mountainhouse',
 'Mountainside',
 'Mountainview',
 'Mountainville',
 'Mountian View',
 'Mountlake Terrace',
 'Mountlake terrace',
 'Mountt Holly',
 'Moutain View',
 'Moyock',
 'Mr. Clemens',
 'Ms State',
 'Mt Airy',
 'Mt Horeb',
 'Mt LAUREL',
 'Mt Laurel',
 'Mt Laurel Township',
 'Mt Pleasant',
 'Mt Prospect',
 'Mt Vernon',
 'Mt&nbsp;Laurel',
 'Mt. Airy',
 'Mt. Arlington',
 'Mt. Clemens',
 'Mt. Holly',
 'Mt. Horeb',
 'Mt. Ida',
 'Mt. Juliet',
 'Mt. Kisco',
 'Mt. Kisko',
 'Mt. Laurel',
 'Mt. Laurel Township',
 'Mt. Olive',
 'Mt. Pleasant',
 'Mt. Prospect',
 'Mt. Sinai',
 'Mt. Sterling',
 'Mt. Vernon',
 'Mt. Washington',
 'Mt.Laurel',
 'Mukilteo',
 'Mulberry',
 'Mulino',
 'Mullica Hill',
 'Mullins',
 'Muncie',
 'Mundelein',
 'Munford',
 'Munhall',
 'Munnsville',
 'Munster',
 'Murdock',
 'Murfreesboro',
 'Murphy',
 'Murphysboro',
 'Murray',
 'Murray Hall',


 'SugarLand',
 'Sugarland',
 'Suite # 135',
 'Suite 100',
 'Suite 1000',
 'Suite 101',
 'Suite 114B',
 'Suite 120',
 'Suite 1203',
 'Suite 132',
 'Suite 1400',
 'Suite 1700',
 'Suite 200 North',
 'Suite 203-D',
 'Suite 210 C',
 'Suite 214',
 'Suite 223',
 'Suite 225',
 'Suite 2300',
 'Suite 2400',
 'Suite 300',
 'Suite 305',
 'Suite 306',
 'Suite 400',
 'Suite 4175',
 'Suite 422',
 'Suite 4B',
 'Suite A200',
 'Suite C2',
 'Suite J',
 'Suite# E',
 'Suitland',
 'Suitland-Silver Hill',
 'Sullivan',
 'Sulpher',
 'Sulphur',
 'Sulphur Spring',
 'Sulphur Springs',
 'Summerland Key',
 'Summersville',
 'Summerville',
 'Summi',
 'Summit',
 'Sumter',
 'Sumter City',
 'Sun City',
 'Sun Prairie',
 'Sun Valley',
 'Sunbury',
 'Sunderland',
 'Sunland',
 'Sunnvale',
 'Sunny Isles Beach',
 'Sunny Vale',
 'SunnyVale',
 'Sunnyavle',
 'Sunnyside',
 'Sunnyvae',
 'Sunnyvale',
 'Sunnyvale Dr',
 'Sunnyvale,',
 'Sunnyvale, CA',
 'Sunnyvalle',
 'Sunnywale',
 'Sunrise',
 'Sunset Hills',
 'Sunyvale',
 'Superior',


In [9]:
cleaned = set([addr_abbrev_replace(l) for l in unique_addr])
print(len(cleaned))
pp.pprint(sorted(cleaned))

107782
['',
 '0 Nationwide Plaza',
 '0. Wayne Rollins Research Center',
 '00 Building',
 '00 Grant Street',
 '0001 Van Dyke Avenue',
 '002 3039 Cornwallis Road',
 '002 Caldwell Building',
 '003 Riverpoint',
 '01 100 N. 18Th Street',
 '01 143G',
 '01 3001 Darrell Road',
 '01 38Th Avenue',
 '01 Atrium Ii North Tower Suite',
 '01 Harper Drive',
 '01 Queens Plaza N',
 '01 Queens Plaza North',
 '01 Research Boulevard',
 '0104 Davey Laboratory',
 '0108 Research Unit A',
 '0111 San Jose Drive',
 '01325 Route 31 South',
 '01512 Ll Pfp',
 '017 Room',
 '018 Cocke Hall',
 '02 100 Tractor Drive Building Cv',
 '0210 Highland Manor Drive',
 '025 5 Kit Creek Road Research Triangle Park',
 '028 Ridge Road',
 '03 2240 1 University Of New Mexico Albuquerque',
 '03 Bldg',
 '03 Building',
 '0305 Life Sciences Bldg',
 '0305A Keller Building',
 '0345 West End Village 221 31St Ave N',
 '0359 201 Centennial Avenue',
 '03F',
 '04 14009 Old Galena Rd. Bldg E Tech Center',
 '04 300 Holger Way',
 '0450 W 750 N',


 '100 Ridge Road',
 '100 Ring Road',
 '100 Riser Road',
 '100 Ritchie Road',
 '100 River Park Drive',
 '100 River Place',
 '100 River Street',
 '100 Riverpark Drive',
 '100 Riverside Drive',
 '100 Rockafeller Road',
 '100 Rockford Drive',
 '100 Rodlphe Street',
 '100 Rodolphe Street',
 '100 Rollins Road',
 '100 Roscommon Drive',
 '100 Route 206 N',
 '100 Route 206 N Pfizer Way',
 '100 Route 206 North',
 '100 Route 206 North Pfizer Way',
 '100 Rowland Way',
 '100 Rue Charlemagne',
 '100 Ryobi Drive',
 '100 S 19Th Street',
 '100 S 4Th Street',
 '100 S 5Th Street',
 '100 S 6Th Street',
 '100 S Biscayne Blvd Suite',
 '100 S Broad Street',
 '100 S Cincinnati Avenue',
 '100 S Clinton St. 8Th Floor',
 '100 S Delaware Boulevard',
 '100 S Ellsworth Avenue',
 '100 S French Street',
 '100 S King Street',
 '100 S Main Street',
 '100 S Mall Arterial',
 '100 S Milwaukee Avenue',
 '100 S Missouri Avenue',
 '100 S Murphy Avenue',
 '100 S Pearl Street',
 '100 S State Street',
 '100 S W 22Nd Avenue',
 '

 '1036 Ross Avenue',
 '1036 S. Jupiter Road',
 '1036 South East Stark Street',
 '1036 W Southern Avenue',
 '10360 Ne 38Th Place',
 '10361 N. Morgan Boulevard',
 '10365 Sanden Drive',
 '10368 W Centennial Road',
 '10368 Westmoor Drive',
 '1037 100Th Street',
 '1037 Benay Road',
 '1037 Cassini Drive Apt F',
 '1037 Raymond Boulevard',
 '1037 Sir Timothy Drive',
 '1037 Sterling Road',
 '1037 W Vernon Avenue',
 '1037 Walnut Avenue',
 '10370 Richmond Avenue',
 '10375 Jefferson Boulevard',
 '10375 Professional Cir',
 '10375 Professional Circle',
 '10375 Richmond Avenue',
 '10379 Forest Brook Lane Apt E',
 '1038 East Chestnut Avenue',
 '1038 Hermosa Avenue',
 '1038 Leigh Avenue',
 '1038 Pendleton Court',
 '1038 Post Street',
 '1038 Princeton Drive',
 '1038 San Jacinto Drive',
 '1038 U.S. Highway',
 '1038 W. Sycamore Road',
 '1038 Whetstone Way',
 '10380 Bren Road West',
 '10381 Citation Drive',
 '10385 Bandley Drive',
 '10385 Colgate Court',
 '10385 Westmoor Drive',
 '10388 Tobias Lane',
 '103

 '110W 40Th Steet',
 '111 /8Th Avenue',
 '111 113 Morgan Way',
 '111 148Th Pl Sw',
 '111 15011 Ne 36Th Street',
 '111 19Th Street',
 '111 21St Avenue South',
 '111 2Nd Avenue Ne',
 '111 8Th Av',
 '111 8Th Ave 13Th Floor',
 '111 8Th Avenue',
 '111 8Th Avenue E',
 '111 8Th Avenue New York',
 '111 8Th. Avenue',
 '111 Academy Drive',
 '111 Adams Road',
 '111 Anza Blvd. Suite',
 '111 Anza Boulevard',
 '111 Bagby Street',
 '111 Barclay Boulevard',
 '111 Bauer Drive',
 '111 Beverly Hills Ter',
 '111 Birch Street',
 '111 Bright Street',
 '111 Broadway',
 '111 Broadway Suite',
 '111 Canal Street',
 '111 Cayuga Drive',
 '111 Center Street',
 '111 Central Avenue',
 '111 Charlotte Place',
 '111 Chestnut Street',
 '111 Cheyenne Drive',
 '111 Chimney Rock Road',
 '111 Church Street Se',
 '111 Colchester Avenue',
 '111 Commerce Road',
 '111 Congress Avenue',
 '111 Continental Drive',
 '111 Coolidge Street',
 '111 Corporate Boulevard',
 '111 Corporate Office Drive',
 '111 Cosma Drive',
 '111 Costumer 

 '11941 Misty Cove Court',
 '11945 Rivera Road',
 '11948 Miramar Parkway',
 '1195 Bordeaux Drive',
 '1195 N Spring Creek Place',
 '1195 Ne Compton Drive',
 '1195 River Drive',
 '1195 River Road',
 '1195 Technology Drive',
 '11950 Corporate Boulevard',
 '11950 Democracy Drive',
 '11950 Jollyville Road',
 '11950 New Kings Road',
 '11950 Parkview Lane',
 '11951 Freedom Dr Ste',
 '11951 Freedom Dr Suite',
 '11951 Freedom Drive',
 '11951 Freedom Road',
 '11953 Market Street',
 '11955 Democracy',
 '11955 Democracy Drive',
 '11955 Demoracy Drive',
 '11955 Freedom Drive',
 '11958 Monarch Street',
 '1196 Borregas Avenue',
 '1196 Third Avenue',
 '1196 W. Boughton Road',
 '1196 Washington Street',
 '11960 Sw 144Th Street',
 '11962 County Road',
 '11966 Sweetwater Drive',
 '11966 Washington Boulevard',
 '1197 Alexander Bnd',
 '1197 E. Arques Avenue',
 '11970 Pellicano Dr. Ste',
 '11971 Foundation Place',
 '11971 Westline Industrial Drive',
 '11973 Foundation Place',
 '11975 El Camino Real',
 '1197

...

 '701 19Th Street South',
 '701 1St Avenue',
 '701 20Th St. S',
 '701 20Th Street South',
 '701 220Th Street Sw',
 '701 22Nd Street',
 '701 3 Mile Rd Nw',
 '701 3 Mile Road Nw',
 '701 32 Nd St South',
 '701 32Nd St S',
 '701 32Nd St South',
 '701 32Nd St. S',
 '701 32Nd Street',
 '701 32Nd Street S',
 '701 32Nd Street South',
 '701 5Th Ave Columbia Center',
 '701 5Th Ave Suite 1600 Ms',
 '701 5Th Avenue',
 '701 9Th St Nw',
 '701 9Th St. Nw',
 '701 9Th Street',
 '701 9Th Street Northweast',
 '701 9Th Street Northwest',
 '701 9Th Street Nw',
 '701 Alpha Drive',
 '701 Aplha Drive',
 '701 B Street',
 '701 Brazos',
 '701 Brazos Street',
 '701 Brickell Avenue',
 '701 Bricknell Avenue',
 '701 Canyon Drive',
 '701 Carlson Parkway',
 '701 Carnegie Center',
 '701 Cashua Ferry Road',
 '701 Centre Avenue',
 '701 Cesar Chavez Street',
 '701 Cool Springs Boulevard',
 '701 Corporate Center',
 '701 Corporate Center Drive',
 '701 Corporate Drive',
 '701 Crestdale Road',
 '701 Daniel Webster Highway',
 

 '7600 Boone Avenue',
 '7600 Burnet Road',
 '7600 C N. Capital Of Texas Hwy',
 '7600 Carroll Avenue',
 '7600 Central Avenue',
 '7600 Chevy Chase Drive',
 '7600 Commerce Park',
 '7600 Dorsey Run Road',
 '7600 Dublin Boulevard',
 '7600 E Caley Avenue',
 '7600 E. Florentine',
 '7600 E.Caley Avenue',
 '7600 East Caley Avenue',
 '7600 East Orchard Road',
 '7600 Flower Avenue',
 '7600 Gateway Boulevard',
 '7600 Jericho Tpke',
 '7600 Kirby Drive',
 '7600 Leesburg Pike',
 '7600 Leesburg Pike West',
 '7600 Lyons Road',
 '7600 Metro Boulevard',
 '7600 Metropolis Drive',
 '7600 Morgan Road',
 '7600 Morgon Road',
 '7600 N. 10Th Street',
 '7600 N. Capital Of Texas Hwy',
 '7600 Ne 41St Street',
 '7600 Northwest 5 Place',
 '7600 Nw 5Th Place',
 '7600 Nw 69Th Avenue',
 '7600 Office Plaza Road',
 '7600 Pearl Street',
 '7600 S Jones Boulevard',
 '7600 W Sunrise Boulevard',
 '7600 W. Sunrise Boulevard',
 '7600 W. Tidwell Road',
 '7600 West Sunrise Boulevard',
 '7600 Whitepine Road',
 '7600 Wisconsin Aven

 '8140 Walnut Hill Lane Suite',
 '8140 Ward Parkway',
 '8143 Agora Parkway',
 '8144 Walnut Hill Lane',
 '8144 Walnut Hill Ln Ste',
 '8145 Flint Street',
 '8145 Highway 6 S',
 '8145 Lewis Road',
 '8145 Se 6Th Avenue',
 '8146 Night Bluff Drive',
 '8148 Genesee Avenue',
 '815 11Th',
 '815 11Th Avenue',
 '815 2Nd Avenue',
 '815 Arnold Drive',
 '815 Berry Street',
 '815 Bonnie Lane',
 '815 Brazos Street',
 '815 Chestnut Street',
 '815 Colorado Avenue',
 '815 Columbia Avenue',
 '815 Connecticut Avenue',
 '815 Connecticut Avenue N.W',
 '815 E Fremont Avenue',
 '815 E Middlefield Road',
 '815 E Wells Fargo Trl',
 '815 East Butler Road',
 '815 East Fremont Avenue',
 '815 East Liberty Street',
 '815 East Pilot Road',
 '815 East Wells Fargo Trail',
 '815 Eleventh Avenue',
 '815 Freeport Road',
 '815 Huey P. Long Avenue',
 '815 Jefferson Boulevard',
 '815 Main Street',
 '815 Market Street',
 '815 Martin Street',
 '815 Mountain Avenue',
 '815 N Broadway',
 '815 N Royal Street',
 '815 N. Broadway',


 '9 260 East Tasman Drive',
 '9 3 4800 Deerwood Pakrway Boulevard',
 '9 30659 Forest Street',
 '9 750 Holiday Drive',
 '9 9 The Embarcadero',
 '9 Argyle Court',
 '9 Banta Place',
 '9 Bauer Lane',
 '9 Camp Street',
 '9 Campus Drive',
 '9 Charlton Street',
 '9 Circuit Drive',
 '9 Clyde Road',
 '9 Cody Road',
 '9 Commercial Street',
 '9 Commodore Drive',
 '9 Corporate Park',
 '9 Corporate Woods',
 '9 Crestview Lane',
 '9 Crosby Drive',
 '9 Crosby Street',
 '9 Cummings Park Drive',
 '9 Cushing',
 '9 Cushing Street',
 '9 Davis Dr Research Triangle Park',
 '9 Davis Drive',
 '9 Davison Avenue',
 '9 Deepark Drive',
 '9 Deer Park Drive',
 '9 E 37Th Street',
 '9 E53Rd Street',
 '9 East 37 Street',
 '9 East 38Th Street',
 '9 East 45Th Street',
 '9 East 47Th Street',
 '9 East Main Street',
 '9 Entin Road',
 '9 Exchange Place',
 '9 Executive Circle',
 '9 Executive Drive Suite',
 '9 Farm Colony Drive',
 '9 Farm Spring Road',
 '9 Farm Springs',
 '9 Farm Springs Road',
 '9 Farmsprings',
 '9 First Amer

 '9631 Fontainebleau Boulevard',
 '9631 Irondale Avenue',
 '9632 Burnet Isle Drive',
 '9632 Conant Street',
 '9633 S. 48Th Street',
 '9635 Granite Ridge Drive',
 '9636 Gudelsky Drive',
 '9639 Telstar Avenue',
 '964 Lake Baldwin Lane',
 '964 Madison Avenue',
 '9640 Bayport Boulevard',
 '9640 Beverly Road',
 '9640 Granite Drive',
 '9640 Granite Ridge Drive',
 '9640 N 31St Avenue',
 '9644 153Rd Ave Ne',
 '9644 153Rd Avenue N.E',
 '9645 Telstar Avenue',
 '9646 Butterfield Way',
 '9649 Beckett Drive',
 '9649 North Freeway',
 '965 Atlantic Avenue',
 '965 Chesterbrook Boulevard',
 '965 Elm Commons Drive',
 '965 Foothill Boulevard',
 '965 Greentree Road',
 '965 Keynote Circle',
 '965 Market Street',
 '965 Mission Street',
 '965 Ridge Lake Boulevard',
 '965 S Billings Way',
 '965 Smokey Road',
 '965 Sterling Lane',
 '965 Trade Center Drive',
 '965 W Chicago Avenue',
 '965 W. Chicago Avenue',
 '965 W. Maude Avenue',
 '965 Wells Street',
 '9650 15Th Ave. Sw',
 '9650 Buffalo Avenue',
 '9650 Cushin

In [ ]:
my_dict = {i: temp.count(i) for i in temp}
pp.pprint(sorted(my_dict.items(), key=lambda x: x[1], reverse=True))

In [296]:
clean_df['VISA_CLASS'].unique()

array(['H-1B', 'E-3 Australian', 'H-1B1 Singapore', 'H-1B1 Chile'],
      dtype=object)

In [ ]:
bin_values = [5000 * i for i in range(1, 100)]

plt.figure(figsize=(12, 4), dpi=100) # 640 x 450
plt.hist(clean_df[clean_df['SOC_CODE'] == '25-1021']['WAGE_RATE_ANNUAL'], bins=bin_values)
plt.show()

In [295]:
clean_df.columns

Index(['VISA_CLASS', 'CASE_STATUS', 'SOC_TITLE', 'SOC_CODE', 'NAICS_CODE',
       'EMPLOYER_NAME', 'AGENT_ATTORNEY_LAW_FIRM', 'WORKSITE_ADDRESS1',
       'WORKSITE_ADDRESS2', 'WORKSITE_CITY', 'WORKSITE_COUNTY',
       'WORKSITE_STATE', 'WORKSITE_POSTAL_CODE', 'WAGE_RATE_OF_PAY_FROM',
       'WAGE_RATE_OF_PAY_TO', 'WAGE_UNIT_OF_PAY', 'PREVAILING_WAGE',
       'PW_UNIT_OF_PAY', 'PW_TRACKING_NUMBER', 'PW_WAGE_LEVEL', 'PW_OES_YEAR',
       'PW_OTHER_SOURCE', 'PW_NON-OES_YEAR', 'WAGE_RATE_ANNUAL',
       'PREVAILING_WAGE_RATE_ANNUAL', 'WORKSITE_ADDRESS_CLEAN',
       'WORKSITE_CITY_CLEAN'],
      dtype='object')

In [328]:
useful_df = clean_df[['VISA_CLASS', 'CASE_STATUS', 
                      'SOC_TITLE', 'SOC_CODE', 'NAICS_CODE',
                      'EMPLOYER_NAME', 'AGENT_ATTORNEY_LAW_FIRM',
                      'WORKSITE_ADDRESS_CLEAN', 'WORKSITE_CITY_CLEAN', 'WORKSITE_STATE', 'WORKSITE_POSTAL_CODE',
                      'WAGE_RATE_ANNUAL', 'PREVAILING_WAGE_RATE_ANNUAL', 'PW_WAGE_LEVEL', 'PW_OES_YEAR',
                     ]]
useful_df = useful_df[(useful_df['CASE_STATUS'] == 'CERTIFIED') & (useful_df['VISA_CLASS'] == 'H-1B') ]
print(len(useful_df))

578640


In [329]:
#for i, row in tqdm.tqdm(useful_df.iterrows(), total=len(df2), miniters=int(10000)):
#    gps_key = tuple(row[['WORKSITE_ADDRESS_CLEAN', 'WORKSITE_CITY_CLEAN', 'WORKSITE_POSTAL_CODE']])
#    if gps_key in address_lookup and address_lookup[gps_key] is not None:
#        gps = address_lookup[gps_key]
#        row['LATITUDE'] = gps[0]
#        row['LONGITUDE'] = gps[1]

def find_gps(row):
    # print(row)
    gps_key = tuple(row[['WORKSITE_ADDRESS_CLEAN', 'WORKSITE_CITY_CLEAN', 'WORKSITE_POSTAL_CODE']])
    if gps_key in address_lookup and address_lookup[gps_key] is not None:
        # print('--')
        gps = address_lookup[gps_key]
        # row['LATITUDE'] = gps[0]
        # row['LONGITUDE'] = gps[1]
        return gps

tqdm.tqdm.pandas()
useful_df['GPS'] = useful_df.progress_apply(lambda row: find_gps(row), axis=1)

/home/jingbo/anaconda3/lib/python3.7/site-packages/tqdm/std.py:658: FutureWarning: The Panel class is removed from pandas. Accessing it from the top-level namespace will also be removed in the next version
  from pandas import Panel









  0%|          | 0/578640 [00:00<?, ?it/s]








  0%|          | 1/578640 [00:00<71:49:50,  2.24it/s]








  0%|          | 321/578640 [00:00<50:16:07,  3.20it/s]








  0%|          | 641/578640 [00:00<35:11:01,  4.56it/s]








  0%|          | 971/578640 [00:00<24:37:45,  6.52it/s]








  0%|          | 1301/578640 [00:00<17:14:42,  9.30it/s]








  0%|          | 1632/578640 [00:00<12:04:45, 13.27it/s]








  0%|          | 1961/578640 [00:01<8:27:55, 18.92it/s] 








  0%|          | 2293/578640 [00:01<5:56:12, 26.97it/s]








  0%|          | 2624/578640 [00:01<4:10:04, 38.39it/s]








  1%|          | 2956/578640 [00:01<2:55:49, 54.57it/s]








  1%|          | 3281/578640 [00:01<2:03:53, 77.40it/s]








  

  5%|▍         | 28434/578640 [00:09<02:47, 3292.51it/s]








  5%|▍         | 28764/578640 [00:09<02:47, 3288.20it/s]








  5%|▌         | 29093/578640 [00:09<02:47, 3281.57it/s]








  5%|▌         | 29422/578640 [00:09<02:47, 3275.74it/s]








  5%|▌         | 29752/578640 [00:09<02:47, 3282.32it/s]








  5%|▌         | 30084/578640 [00:09<02:46, 3291.64it/s]








  5%|▌         | 30414/578640 [00:09<02:46, 3283.19it/s]








  5%|▌         | 30747/578640 [00:09<02:46, 3294.83it/s]








  5%|▌         | 31079/578640 [00:09<02:45, 3299.66it/s]








  5%|▌         | 31413/578640 [00:09<02:45, 3310.56it/s]








  5%|▌         | 31745/578640 [00:10<02:45, 3311.67it/s]








  6%|▌         | 32077/578640 [00:10<02:45, 3301.27it/s]








  6%|▌         | 32410/578640 [00:10<02:45, 3308.80it/s]








  6%|▌         | 32741/578640 [00:10<02:44, 3308.77it/s]








  6%|▌         | 33072/578640 [00:10<02:45, 3300.69it/s]








  6%|▌         | 33404/57

 10%|█         | 58025/578640 [00:18<02:37, 3303.92it/s]








 10%|█         | 58360/578640 [00:18<02:36, 3317.24it/s]








 10%|█         | 58693/578640 [00:18<02:36, 3319.45it/s]








 10%|█         | 59028/578640 [00:18<02:36, 3328.40it/s]








 10%|█         | 59361/578640 [00:18<02:36, 3315.72it/s]








 10%|█         | 59693/578640 [00:18<02:36, 3308.49it/s]








 10%|█         | 60024/578640 [00:18<02:36, 3306.12it/s]








 10%|█         | 60355/578640 [00:18<02:36, 3301.30it/s]








 10%|█         | 60689/578640 [00:18<02:36, 3311.34it/s]








 11%|█         | 61021/578640 [00:18<02:36, 3310.90it/s]








 11%|█         | 61357/578640 [00:19<02:35, 3323.42it/s]








 11%|█         | 61690/578640 [00:19<02:35, 3315.55it/s]








 11%|█         | 62022/578640 [00:19<02:36, 3308.33it/s]








 11%|█         | 62353/578640 [00:19<02:36, 3296.19it/s]








 11%|█         | 62685/578640 [00:19<02:36, 3302.29it/s]








 11%|█         | 63016/57

 15%|█▌        | 87598/578640 [00:26<02:28, 3308.18it/s]








 15%|█▌        | 87929/578640 [00:27<02:28, 3293.76it/s]








 15%|█▌        | 88259/578640 [00:27<02:28, 3293.48it/s]








 15%|█▌        | 88589/578640 [00:27<02:29, 3286.56it/s]








 15%|█▌        | 88922/578640 [00:27<02:28, 3296.77it/s]








 15%|█▌        | 89252/578640 [00:27<02:28, 3290.51it/s]








 15%|█▌        | 89584/578640 [00:27<02:28, 3298.39it/s]








 16%|█▌        | 89914/578640 [00:27<02:28, 3289.71it/s]








 16%|█▌        | 90243/578640 [00:27<02:28, 3288.78it/s]








 16%|█▌        | 90572/578640 [00:27<02:28, 3282.14it/s]








 16%|█▌        | 90901/578640 [00:27<02:28, 3283.97it/s]








 16%|█▌        | 91233/578640 [00:28<02:28, 3292.53it/s]








 16%|█▌        | 91565/578640 [00:28<02:27, 3298.55it/s]








 16%|█▌        | 91897/578640 [00:28<02:27, 3304.83it/s]








 16%|█▌        | 92228/578640 [00:28<02:27, 3294.06it/s]








 16%|█▌        | 92559/57

 20%|██        | 116756/578640 [00:35<02:19, 3316.68it/s]








 20%|██        | 117088/578640 [00:35<02:19, 3297.11it/s]








 20%|██        | 117418/578640 [00:36<02:20, 3282.24it/s]








 20%|██        | 117753/578640 [00:36<02:19, 3300.04it/s]








 20%|██        | 118086/578640 [00:36<02:19, 3306.77it/s]








 20%|██        | 118417/578640 [00:36<02:19, 3299.54it/s]








 21%|██        | 118752/578640 [00:36<02:18, 3312.32it/s]








 21%|██        | 119085/578640 [00:36<02:18, 3317.58it/s]








 21%|██        | 119417/578640 [00:36<02:18, 3306.37it/s]








 21%|██        | 119750/578640 [00:36<02:18, 3312.32it/s]








 21%|██        | 120082/578640 [00:36<02:18, 3306.01it/s]








 21%|██        | 120415/578640 [00:36<02:18, 3313.03it/s]








 21%|██        | 120750/578640 [00:37<02:17, 3322.24it/s]








 21%|██        | 121083/578640 [00:37<02:18, 3312.35it/s]








 21%|██        | 121416/578640 [00:37<02:17, 3317.44it/s]








 21%|██   

...

 76%|███████▌  | 437758/578640 [02:13<00:42, 3306.73it/s]








 76%|███████▌  | 438089/578640 [02:13<00:42, 3295.60it/s]








 76%|███████▌  | 438421/578640 [02:13<00:42, 3301.68it/s]








 76%|███████▌  | 438752/578640 [02:13<00:42, 3301.17it/s]








 76%|███████▌  | 439086/578640 [02:13<00:42, 3312.21it/s]








 76%|███████▌  | 439418/578640 [02:13<00:42, 3303.33it/s]








 76%|███████▌  | 439749/578640 [02:13<00:42, 3272.31it/s]








 76%|███████▌  | 440077/578640 [02:13<00:42, 3263.52it/s]








 76%|███████▌  | 440405/578640 [02:13<00:42, 3266.40it/s]








 76%|███████▌  | 440732/578640 [02:14<00:42, 3255.50it/s]








 76%|███████▌  | 441066/578640 [02:14<00:41, 3280.23it/s]








 76%|███████▋  | 441397/578640 [02:14<00:41, 3287.88it/s]








 76%|███████▋  | 441726/578640 [02:14<00:41, 3287.37it/s]








 76%|███████▋  | 442055/578640 [02:14<00:41, 3286.30it/s]








 76%|███████▋  | 442386/578640 [02:14<00:41, 3289.48it/s]








 77%|█████

 81%|████████  | 466950/578640 [02:22<00:33, 3303.66it/s]








 81%|████████  | 467281/578640 [02:22<00:33, 3304.70it/s]








 81%|████████  | 467612/578640 [02:22<00:33, 3305.08it/s]








 81%|████████  | 467944/578640 [02:22<00:33, 3308.37it/s]








 81%|████████  | 468277/578640 [02:22<00:33, 3313.83it/s]








 81%|████████  | 468609/578640 [02:22<00:33, 3314.41it/s]








 81%|████████  | 468941/578640 [02:22<00:33, 3308.30it/s]








 81%|████████  | 469272/578640 [02:22<00:33, 3308.29it/s]








 81%|████████  | 469603/578640 [02:22<00:33, 3292.96it/s]








 81%|████████  | 469933/578640 [02:22<00:33, 3290.12it/s]








 81%|████████▏ | 470265/578640 [02:23<00:32, 3298.38it/s]








 81%|████████▏ | 470595/578640 [02:23<00:32, 3285.77it/s]








 81%|████████▏ | 470924/578640 [02:23<00:32, 3274.58it/s]








 81%|████████▏ | 471253/578640 [02:23<00:32, 3278.00it/s]








 81%|████████▏ | 471585/578640 [02:23<00:32, 3287.86it/s]








 82%|█████

 86%|████████▌ | 496156/578640 [02:30<00:25, 3289.41it/s]








 86%|████████▌ | 496489/578640 [02:30<00:24, 3299.57it/s]








 86%|████████▌ | 496820/578640 [02:31<00:24, 3301.89it/s]








 86%|████████▌ | 497151/578640 [02:31<00:24, 3288.60it/s]








 86%|████████▌ | 497480/578640 [02:31<00:24, 3286.82it/s]








 86%|████████▌ | 497809/578640 [02:31<00:24, 3272.60it/s]








 86%|████████▌ | 498137/578640 [02:31<00:24, 3271.43it/s]








 86%|████████▌ | 498468/578640 [02:31<00:24, 3281.81it/s]








 86%|████████▌ | 498797/578640 [02:31<00:24, 3279.62it/s]








 86%|████████▋ | 499128/578640 [02:31<00:24, 3288.34it/s]








 86%|████████▋ | 499457/578640 [02:31<00:24, 3286.81it/s]








 86%|████████▋ | 499789/578640 [02:31<00:23, 3293.87it/s]








 86%|████████▋ | 500121/578640 [02:32<00:23, 3299.45it/s]








 86%|████████▋ | 500452/578640 [02:32<00:23, 3300.67it/s]








 87%|████████▋ | 500783/578640 [02:32<00:23, 3298.68it/s]








 87%|█████

 91%|█████████ | 525372/578640 [02:39<00:16, 3299.74it/s]








 91%|█████████ | 525703/578640 [02:39<00:16, 3302.24it/s]








 91%|█████████ | 526040/578640 [02:39<00:15, 3322.15it/s]








 91%|█████████ | 526375/578640 [02:39<00:15, 3328.88it/s]








 91%|█████████ | 526708/578640 [02:40<00:15, 3323.50it/s]








 91%|█████████ | 527042/578640 [02:40<00:15, 3327.77it/s]








 91%|█████████ | 527375/578640 [02:40<00:15, 3324.38it/s]








 91%|█████████ | 527708/578640 [02:40<00:15, 3320.80it/s]








 91%|█████████▏| 528041/578640 [02:40<00:15, 3322.13it/s]








 91%|█████████▏| 528378/578640 [02:40<00:15, 3334.23it/s]








 91%|█████████▏| 528712/578640 [02:40<00:15, 3326.76it/s]








 91%|█████████▏| 529045/578640 [02:40<00:14, 3306.35it/s]








 91%|█████████▏| 529380/578640 [02:40<00:14, 3317.63it/s]








 92%|█████████▏| 529712/578640 [02:40<00:14, 3298.55it/s]








 92%|█████████▏| 530045/578640 [02:41<00:14, 3305.70it/s]








 92%|█████

 96%|█████████▌| 554583/578640 [02:48<00:07, 3311.82it/s]








 96%|█████████▌| 554915/578640 [02:48<00:07, 3307.97it/s]








 96%|█████████▌| 555248/578640 [02:48<00:07, 3311.67it/s]








 96%|█████████▌| 555580/578640 [02:48<00:06, 3313.00it/s]








 96%|█████████▌| 555916/578640 [02:48<00:06, 3324.72it/s]








 96%|█████████▌| 556249/578640 [02:49<00:06, 3318.70it/s]








 96%|█████████▌| 556582/578640 [02:49<00:06, 3321.42it/s]








 96%|█████████▌| 556915/578640 [02:49<00:06, 3264.43it/s]








 96%|█████████▋| 557242/578640 [02:49<00:06, 3251.17it/s]








 96%|█████████▋| 557571/578640 [02:49<00:06, 3259.92it/s]








 96%|█████████▋| 557899/578640 [02:49<00:06, 3264.66it/s]








 96%|█████████▋| 558226/578640 [02:49<00:06, 3262.69it/s]








 97%|█████████▋| 558560/578640 [02:49<00:06, 3283.47it/s]








 97%|█████████▋| 558895/578640 [02:49<00:05, 3301.16it/s]








 97%|█████████▋| 559226/578640 [02:49<00:05, 3294.10it/s]








 97%|█████

In [331]:
useful_df.head(100)

VISA_CLASS CASE_STATUS                           SOC_TITLE SOC_CODE  \
24        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
26        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
47        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
52        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
54        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
55        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
56        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
57        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
72        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
73        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
75        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
79        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
84        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
87        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
88        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
93        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
94        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
96        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
97        H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
106       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
107       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
111       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
120       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
121       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
122       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
128       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
130       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
131       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
132       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
133       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
136       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
139       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
140       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
141       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
142       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
143       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
144       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
146       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
147       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
148       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
149       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
150       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
151       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
152       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
153       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
154       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
155       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
156       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
157       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
158       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
160       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
161       H-1B   CERTIFIED  ADVERTISING AND PROMOTIONS MANAGER  11-2011   
162       H-1B   CERTIFIED  A

In [338]:
pickle.dump(useful_df, open('useful_df.pickle', 'wb'))

In [337]:
import utils
utils.__dict__

{'__name__': 'utils',
 '__doc__': None,
 '__package__': '',
 '__loader__': <_frozen_importlib_external.SourceFileLoader at 0x7fa9f090fd10>,
 '__spec__': ModuleSpec(name='utils', loader=<_frozen_importlib_external.SourceFileLoader object at 0x7fa9f090fd10>, origin='/mnt/c/Users/jingb/GoogleDrive/SourceCode/h1b_parser/utils.py'),
 '__file__': '/mnt/c/Users/jingb/GoogleDrive/SourceCode/h1b_parser/utils.py',
 '__cached__': '/mnt/c/Users/jingb/GoogleDrive/SourceCode/h1b_parser/__pycache__/utils.cpython-37.pyc',
 '__builtins__': {'__name__': 'builtins',
  '__doc__': "Built-in functions, exceptions, and other objects.\n\nNoteworthy: None is the `nil' object; Ellipsis represents `...' in slices.",
  '__package__': '',
  '__loader__': _frozen_importlib.BuiltinImporter,
  '__spec__': ModuleSpec(name='builtins', loader=<class '_frozen_importlib.BuiltinImporter'>),
  '__build_class__': <function __build_class__>,
  '__import__': <function __import__>,
  'abs': <function abs(x, /)>,
  'all': <funct

In [336]:
jsonfile = utils.get_geojson(['ny', 'nj', 'ct'])

AttributeError: module 'utils' has no attribute 'get_geojson'

In [ ]:
zip_agg['WAGE'][(zip_agg['WAGE'] > 175 * 1000)] = 175 * 1000
zip_agg['WAGE'][(zip_agg['WAGE'] < 60 * 1000)] = 60 * 1000

In [ ]:
map = folium.Map(location=[40.693943, -73.985880], default_zoom_start=12)
#folium.Marker(
#    location=[40.693943, -73.985880],
    # popup='Welcome to <b>NEW YORK CITY</b>',
    # tooltip = "Click for more"
#).add_to(map)


map.choropleth(geo_data=il_json, 
                 data=zip_agg, # my dataset
                 columns=['ZIPCODE', 'WAGE'], # zip code is here for matching the geojson zipcode, sales price is the column that changes the color of zipcode areas
                 key_on='feature.properties.ZCTA5CE10', # this path contains zipcodes in str type, this zipcodes should match with our ZIP CODE column
                 fill_color='BuPu', fill_opacity=0.7, line_opacity=0.2,
                 # bins = value_bins,
                 legend_name='Wage')

# folium.LayerControl().add_to(map)

In [ ]:
display(map)

In [ ]:
map.choropleth.__dict__

In [ ]:

# this line just to force our dataset zipcodes from numbers to strings so they match our geojson file
df['zipcode'] = df['zipcode'].astype('str')


# load my geojson file which contains my Polygons
boundary_file = "geojson_files/Zipcodes_for_King_County_and_Surrounding_Area__Shorelines____zipcode_shore_area.geojson"
with open(boundary_file, 'r') as f:
    zipcode_boundary = json.load(f)

    
# Grab my map center again using our created fucntion (same as before)
center = get_center_latlong(df)


# Initialize Folium Map again (same as before)
m = folium.Map(location=center, 
               zoom_start=10,
               tiles='Stamen Toner')


# Use the groupby method to 
zipcode_data = df.groupby('zipcode').aggregate(np.mean)
zipcode_data.reset_index(inplace = True)


# Create choropleth map  
folium.Choropleth(
    geo_data=zipcode_boundary,
    name='choropleth',
    data=zipcode_data,
    columns=['zipcode', 'price'],
    key_on='feature.properties.ZIPCODE',
    fill_color='Spectral',
    fill_opacity=0.6,
    nan_fill_opacity=0,
    line_opacity=1,
    legend_name='Mean Price'
).add_to(m)


m.save('zipcode_choropleth.html')

In [ ]:
import urllib
import simplejson

googleGeocodeUrl = 'http://maps.googleapis.com/maps/api/geocode/json?'

def get_coordinates(query, from_sensor=False):
    query = query.encode('utf-8')
    params = {
        'address': query,
        'sensor': "true" if from_sensor else "false"
    }
    url = googleGeocodeUrl + urllib.parse.urlencode(params)
    json_response = urllib.request.urlopen(url)
    response = simplejson.loads(json_response.read())
    if response['results']:
        location = response['results'][0]['geometry']['location']
        latitude, longitude = location['lat'], location['lng']
        print (query, latitude, longitude)
    else:
        latitude, longitude = None, None
        print (query, "<no results>")
    return latitude, longitude

In [ ]:
get_coordinates('131 South Dearborn Street, Chicago, IL, 60601')

In [22]:
all_gps = []
# for c in tqdm.tqdm(cleaned):
for c in cleaned:
    gps = get_gps(c)
    all_gps.append(gps)
    if gps is not None:
        print(f'{c}: GPS({gps})')

123 West Madison Street: GPS((39.80415526530612, -89.65515987755103))
13810 Se Eastgate: GPS((1.30436035, 103.90334825))
10604 4 Manhattanville Road: GPS((41.025060720517025, -73.71645220812358))
11400 73Rd Ave. N: GPS((41.5916674, -90.2309553))
2000 Palmyra Road: GPS((41.859847, -83.9324549))
17802 Frontage Road: GPS((39.7579689, -89.6283766))
1 Pershing Plaza: GPS((28.542105, -81.394252))
1 Bryant Park: GPS((10.230611849999999, 77.49228009231106))
10 Tenth Street Nw: GPS((43.6907537, -92.9867573))
3900 10Th Ave. S: GPS((44.932225, -93.260088))
9485 Mentor Avenue: GPS((41.6697704, -81.3322942))
210 11Th Ave Sw: GPS((33.48416683007769, -86.83551285814367))
1177 South Beltline Road: GPS((34.69892725531465, -81.62059207662966))
32 Dixon Drive: GPS((36.51676491956389, -87.35970600988067))
111 Whitney Avenue: GPS((43.2527087, -79.924252))
7025 N. Lilley Road: GPS((42.33535202, -83.4593887))
300 N. Texas Avenue: GPS((31.759386, -106.486148))
570 Glenneyre Street: GPS((33.54065215919727, -11

KeyboardInterrupt: 

In [15]:
all_gps

[(40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.98353680295259),
 (40.75375085, -73.983536802

In [ ]:
from commonregex import CommonRegex
parsed_text = CommonRegex('I live at 400 E. TASMAN DR.')

In [ ]:
parsed_text.street_addresses

In [ ]:
cleaned